## Race / ethnicity for California's 50th Congressional District. 

##### This notebook creates five maps that display race/ethnicity for California's 50th Congressional District using Folium. The racial categories mapped are:
-Latinx

-White alone

-African-American alone

-Asian alone

-other alone. 

The other race category is an aggregate sum of Native Americans, Pacific Islanders, some other race, and two or more races. Their percentages were too small to represent individually. 

Source: Table: B03002: U.S. Census Bureau, 2013-2017 American Community Survey 5-Year Estimates)

##### Source: Table: B03002: U.S. Census Bureau, 2013-2017 American Community Survey 5-Year Estimates)

### Import libraries

In [1]:
import math
import numpy as np
import pandas as pd
import collections
import requests 
from urllib.request import urlopen, Request

import json # for working with JSON data
import geojson # ditto for GeoJSON data - an extension of JSON with support for geographic data
import geopandas as gpd

import matplotlib # base python plotting library
%matplotlib inline  
import matplotlib.pyplot as plt # more plotting stuff 

import folium # popular python web mapping tool for creating Leaflet maps
import folium.plugins
import sys
sys.path.insert(0, 'folium')
sys.path.insert(0, 'branca')

import branca.colormap as cm

In [2]:
print(folium.__version__)

0.10.1


In [3]:
# We are getting futurewarning errors about the syntax of CRS definitions, ie "init=epsg:4269" vs "epsg:4269"
# so suppress as these are minor
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

### Read in the Data

Reading geo data for CA Congressional 50th District.

In [4]:
tracts_gdf = gpd.read_file(r'G:\My Drive\Data\Race Eth ACS 2017\Geo_Files\race_ethn_w_geo.json')

In [5]:
# take a look at all column names
tracts_gdf.columns

Index(['GEOID', 'Census Tract', 'County', 'Total', 'Not_Latino', 'White',
       'Black', 'Asian', 'Latino', 'Other_agg', 'Not_Latino_e_pct',
       'White_e_pct', 'Black_e_pct', 'Asian_e_pct', 'Latino_e_pct',
       'Other_agg_e_pct', 'geometry'],
      dtype='object')

In [6]:
# take a look at one total
tracts_gdf.Black_e_pct.describe()

count    159.000000
mean       2.765333
std        2.566517
min        0.000000
25%        0.948893
50%        1.925457
75%        3.734840
max       12.225381
Name: Black_e_pct, dtype: float64

Getting the centroid of the geography for the inital zoom perspective.

In [7]:
y_1 = tracts_gdf.centroid.y.mean()
y_1

33.07216891451991

In [8]:
x_1 = tracts_gdf.centroid.x.mean()
x_1

-117.01783743412315

In [9]:
tracts_gdf.head(2)

GEOID Census Tract     County  Total  Not_Latino  White  Black  \
0  06065051200       CT 512  Riverside   4002        2250   1749     49   
1  06065049600       CT 496  Riverside   8407        6147   4511    885   

   Asian  Latino  Other_agg  Not_Latino_e_pct  White_e_pct  Black_e_pct  \
0    332    1752        120         56.221889    43.703148     1.224388   
1    388    2260        363         73.117640    53.657666    10.526942   

   Asian_e_pct  Latino_e_pct  Other_agg_e_pct  \
0     8.295852     43.778111         2.998501   
1     4.615202     26.882360         4.317830   

                                            geometry  
0  MULTIPOLYGON (((-117.14876 33.47290, -117.1493...  
1  POLYGON ((-117.16311 33.52238, -117.16311 33.5...

##### Creating Latinx Map

In [10]:

map1= folium.Map(location=[tracts_gdf.centroid.y.mean(), tracts_gdf.centroid.x.mean()], 
                  tiles='CartoDB Positron',
                  width=700,height=500,
                  zoom_start=9)

title_html = '''
             <h3 align="center" style="font-size:20px"><b>Percentage of Latinx in CA 50th Congressional District</b></h3> 
             '''
map1.get_root().html.add_child(folium.Element(title_html))

#----------------------------------------------------------------------------------------------------------------------
# Add the Choropleth layer Latinx
pop1=folium.Choropleth(geo_data=tracts_gdf[['GEOID','geometry']].set_index('GEOID'),
           data=tracts_gdf, # tabular data in this case, it's the same as the geo dataset
           columns=['GEOID', 'Latino_e_pct'], #-----------------------------------------
           fill_color='GnBu',
           fill_opacity=0.65,
           bins=[0,10,20,30,40,100],
           line_color="grey", #"white",
           line_weight=1,
           line_opacity=1,
           key_on="feature.id", # the key to match on if the dataset differed
           legend_name='Latinx',  #-----------------------------------------
           highlight=True
          ).add_to(map1)

# Not_Latino_e_pct	White_e_pct	Black_e_pct	Asian_e_pct	Latino_e_pct	Other_agg_e_pct	
#----------------------------------------------------------------------------------------------------------------------

folium.GeoJson(tracts_gdf,
    style_function=lambda x: {'color':'transparent','fillColor':'transparent'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Census Tract', 'County', 'Latino_e_pct', 'Latino', 'Total'],  #-----------------------------------------
        aliases=['Census Tract:', 'County:', 'Latinx Percentage:','Latinx Total:','Total Population:' ], #-----------------------------------------
        labels=True,
        localize=True
    ),
    highlight_function=lambda x: {'weight':2,'color':'black'}
).add_to(pop1.geojson)

#----------------------------------------------------------------------------------------------------------------------


map1  # show map



##### Creating Map for the White population

In [ ]:

map1= folium.Map(location=[tracts_gdf.centroid.y.mean(), tracts_gdf.centroid.x.mean()], 
                  tiles='CartoDB Positron',
                  width=700,height=500,
                  zoom_start=9)

title_html = '''
             <h3 align="center" style="font-size:20px"><b>Percentage of Whites in CA 50th Congressional District</b></h3>
             '''
map1.get_root().html.add_child(folium.Element(title_html))

#----------------------------------------------------------------------------------------------------------------------
# Add the Choropleth layer 
pop1=folium.Choropleth(geo_data=tracts_gdf[['GEOID','geometry']].set_index('GEOID'),
           data=tracts_gdf, # tabular data in this case, it's the same as the geo dataset
           columns=['GEOID', 'White_e_pct'], #-----------------------------------------
           fill_color='GnBu',
           fill_opacity=0.65,
           bins=[0,10,20,30,40,100],
           line_color="grey", #"white",
           line_weight=1,
           line_opacity=1,
           key_on="feature.id", # the key to match on if the dataset differed
           legend_name='White',  #-----------------------------------------
           highlight=True
          ).add_to(map1)

# Not_Latino_e_pct	White_e_pct	Black_e_pct	Asian_e_pct	Latino_e_pct	Other_agg_e_pct	
#----------------------------------------------------------------------------------------------------------------------

folium.GeoJson(tracts_gdf,
    style_function=lambda x: {'color':'transparent','fillColor':'transparent'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Census Tract', 'County', 'White_e_pct', 'White', 'Total'],  #-----------------------------------------
        aliases=['Census Tract:', 'County:', 'White Percentage:','White Total:','Total Population:' ], #---------------
        labels=True,
        localize=True
    ),
    highlight_function=lambda x: {'weight':2,'color':'black'}
).add_to(pop1.geojson)

#----------------------------------------------------------------------------------------------------------------------


map1  # show map



##### Creating Map for the African American population // The population is so small I used a different color and scale. 

In [ ]:

map1= folium.Map(location=[tracts_gdf.centroid.y.mean(), tracts_gdf.centroid.x.mean()], 
                  tiles='CartoDB Positron',
                  width=700,height=500,
                  zoom_start=9)

title_html = '''
             <h3 align="center" style="font-size:16px"><b>Percentage of African Americans in CA 50th Congressional District</b></h3>
             '''
map1.get_root().html.add_child(folium.Element(title_html))

#----------------------------------------------------------------------------------------------------------------------
# Add the Choropleth layer 
pop1=folium.Choropleth(geo_data=tracts_gdf[['GEOID','geometry']].set_index('GEOID'),
           data=tracts_gdf, # tabular data in this case, it's the same as the geo dataset
           columns=['GEOID', 'Black_e_pct'], #-----------------------------------------
           fill_color='RdPu',
           fill_opacity=0.65,
           bins=[0,5,10,15,20,100],
           line_color="grey", #"white",
           line_weight=1,
           line_opacity=1,
           key_on="feature.id", # the key to match on if the dataset differed
           legend_name='African American',  #-----------------------------------------
           highlight=True
          ).add_to(map1)

# Not_Latino_e_pct	White_e_pct	Black_e_pct	Asian_e_pct	Latino_e_pct	Other_agg_e_pct	
#----------------------------------------------------------------------------------------------------------------------

folium.GeoJson(tracts_gdf,
    style_function=lambda x: {'color':'transparent','fillColor':'transparent'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Census Tract', 'County', 'Black_e_pct', 'Black', 'Total'],  #-----------------------------------------
        aliases=['Census Tract:', 'County:', 'African American %:','African American Total:','Total Population:' ], #---------------
        labels=True,
        localize=True
    ),
    highlight_function=lambda x: {'weight':2,'color':'black'}
).add_to(pop1.geojson)

#----------------------------------------------------------------------------------------------------------------------


map1  # show map



##### Creating Map for the Asian population

In [ ]:

map1= folium.Map(location=[tracts_gdf.centroid.y.mean(), tracts_gdf.centroid.x.mean()], 
                  tiles='CartoDB Positron',
                  width=700,height=500,
                  zoom_start=9)

title_html = '''
             <h3 align="center" style="font-size:20px"><b>Percentage of Asians in CA 50th Congressional District</b></h3>
             '''
map1.get_root().html.add_child(folium.Element(title_html))

#----------------------------------------------------------------------------------------------------------------------
# Add the Choropleth layer 
pop1=folium.Choropleth(geo_data=tracts_gdf[['GEOID','geometry']].set_index('GEOID'),
           data=tracts_gdf, # tabular data in this case, it's the same as the geo dataset
           columns=['GEOID', 'Asian_e_pct'], #-----------------------------------------
           fill_color='GnBu',
           fill_opacity=0.65,
           bins=[0,10,20,30,40,100],
           line_color="grey", #"white",
           line_weight=1,
           line_opacity=1,
           key_on="feature.id", # the key to match on if the dataset differed
           legend_name='Asian American',  #-----------------------------------------
           highlight=True
          ).add_to(map1)

# Not_Latino_e_pct	White_e_pct	Black_e_pct	Asian_e_pct	Latino_e_pct	Other_agg_e_pct	
#----------------------------------------------------------------------------------------------------------------------

folium.GeoJson(tracts_gdf,
    style_function=lambda x: {'color':'transparent','fillColor':'transparent'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Census Tract', 'County', 'Asian_e_pct', 'Asian', 'Total'],  #-----------------------------------------
        aliases=['Census Tract:', 'County:', 'Asian Percentage:','Asian Total:','Total Population:' ], #---------------
        labels=True,
        localize=True
    ),
    highlight_function=lambda x: {'weight':2,'color':'black'}
).add_to(pop1.geojson)

#----------------------------------------------------------------------------------------------------------------------


map1  # show map



##### Creating Map for the Other Racial group population

In [ ]:

map1= folium.Map(location=[tracts_gdf.centroid.y.mean(), tracts_gdf.centroid.x.mean()], 
                  tiles='CartoDB Positron',
                  width=700,height=500,
                  zoom_start=9)

title_html = '''
             <h3 align="center" style="font-size:18px"><b>Percentage of Other Race in CA 50th Congressional District</b></h3>
             '''
map1.get_root().html.add_child(folium.Element(title_html))

#----------------------------------------------------------------------------------------------------------------------
# Add the Choropleth layer 
pop1=folium.Choropleth(geo_data=tracts_gdf[['GEOID','geometry']].set_index('GEOID'),
           data=tracts_gdf, # tabular data in this case, it's the same as the geo dataset
           columns=['GEOID', 'Other_agg_e_pct'], #-----------------------------------------
           fill_color='GnBu',
           fill_opacity=0.65,
           bins=[0,10,20,30,40,100],
           line_color="grey", #"white",
           line_weight=1,
           line_opacity=1,
           key_on="feature.id", # the key to match on if the dataset differed
           legend_name='Other American',  #-----------------------------------------
           highlight=True
          ).add_to(map1)

# Not_Latino_e_pct	White_e_pct	Black_e_pct	Asian_e_pct	Latino_e_pct	Other_agg_e_pct	
#----------------------------------------------------------------------------------------------------------------------

folium.GeoJson(tracts_gdf,
    style_function=lambda x: {'color':'transparent','fillColor':'transparent'},
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Census Tract', 'County', 'Other_agg_e_pct', 'Other_agg', 'Total'],  #-----------------------------------------
        aliases=['Census Tract:', 'County:', 'Other Race Percentage:','Other Total:','Total Population:' ], #---------------
        labels=True,
        localize=True
    ),
    highlight_function=lambda x: {'weight':2,'color':'black'}
).add_to(pop1.geojson)

#----------------------------------------------------------------------------------------------------------------------


map1  # show map

